<table style="text-align: left; width: 100%;" border="0"
 cellpadding="0" cellspacing="0">

  <tbody>
    <tr align="center" style="height: 1px; background-color: rgb(0, 0, 0);">
      <td><img src="https://i.imgur.com/RGV3U0q.png" title="source: imgur.com" /></td>
      <td><big><big><big><big><span style="font-family: Calibri; color: white; font-weight: bold;">Laboratorio III</span></big></big></big></big></td>
      <td><img src="https://i.imgur.com/YOQky86.png" title="source: imgur.com" style="width: 250px; height: auto;" /></td>
    </tr>
    <tr align="center">
      <td colspan="3" rowspan="1"
 style="height: 1px; background-color: rgb(68, 68, 100);"></td>
    </tr>
    <tr align="center">
      <td colspan="3" rowspan="1"><big><big><big><big><span
 style="font-family: Calibri;">Clase2 2024-05-22<br> Ejercicio en Clase</span></big></big></big></big><br>
      </td></tr>
    <tr align="center">       
      <td colspan="3" rowspan="1" style="height: 1px; background-color: rgb(68, 68, 100);"></td>
    </tr>
  </tbody>
</table>


<span style="font-family: Calibri; font-weight: bold; ">Autores:</span>
<br style="font-family: Calibri; font-style: italic;">
<span style="font-family: Calibri; font-style: italic;">aDigital</span>
<div class="footer">&copy; 2024</div>


# Info del Dataset sell-in.txt


El dataset de ventas contiene las siguientes columnas:

1. **periodo**: Representa el período de tiempo en formato `yyyymm` (año y mes).
    - Minimum	2017-01-01 00:00:00
    - Maximum	2019-12-01 00:00:00
2. **customer_id**: Identificación única del cliente.
3. **product_id**: Identificación única del producto.
4. **plan_precios_cuidados**: Indicador binario (0 o 1) que señala si el producto está incluido en el plan de precios cuidados.
5. **cust_request_qty**: Cantidad de producto solicitada por el cliente.
6. **cust_request_tn**: Peso en toneladas solicitado por el cliente.
7. **tn**: Peso en toneladas del producto vendido.

Estas columnas proporcionan información detallada sobre las ventas realizadas en distintos períodos, especificando el cliente, el producto, y las cantidades en unidades y en peso.



# Formula Total Forecast Error

In [1]:
import pandas as pd

def calcular_total_forecast_error(actual, forecast):
    """
    Calcula el Total Forecast Error dado un DataFrame con ventas reales y pronosticadas.

    Parámetros:
    actual (pd.Series): Serie con las ventas reales.
    forecast (pd.Series): Serie con las ventas pronosticadas.

    Retorna:
    float: El Total Forecast Error.
    """
    # Calcular el error absoluto
    abs_error = abs(actual - forecast)
    
    # Calcular el Total Forecast Error
    total_forecast_error = abs_error.sum() / actual.sum()
    
    return total_forecast_error

# Ejemplo de uso
# Crear un DataFrame de ejemplo
data = {
    'product_id': [1, 2, 3, 4, 5],
    'actual_sales': [100, 150, 200, 250, 300],
    'forecast_sales': [110, 145, 190, 260, 310]
}
df = pd.DataFrame(data)

# Calcular el Total Forecast Error
tfe = calcular_total_forecast_error(df['actual_sales'], df['forecast_sales'])
#print(f'Total Forecast Error: {tfe:.2%}')


# Enunciado Prediccion 1 - Prediccion Trivial

Con la data disponible hacer una primera prediccion trivial

## Ej1) Prediccion Entregas (tn) Mayo con datos de Marzo 2019

Con los datos del mes de marzo de 2019 se pide:

1) Predecir cuantas ventas vamos a tener durante el mes de mayo 2019
2) Calcular el error rate


## Ej2) Prediccion Entregas (tn) Mayo 2019 con datos de 6 meses previos

Con los datos de el promedio de ventas de los 6 meses previos al mes de mayo de 2019 se pide:

1) Predecir cuantas ventas vamos a tener durante el mes de mayo 2019
2) Calcular el error rate

In [2]:
##import warnings
##warnings.filterwarnings("ignore")
import numpy as np
from ydata_profiling import ProfileReport
import pandas as pd
#Configuración de parametros de Pandas para mejor visualización
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.precision', 3)
pd.set_option('plotting.backend', 'matplotlib')
pd.options.mode.chained_assignment = None

# Ruta al archivo
#file_path = '../Data/sell-in-ach-muestra.txt'
file_path = '../66_Datos/sell-in.txt'

# Cargar el archivo en un DataFrame
df = pd.read_csv(file_path, sep='\t')

# Codigo si necesito guardar el df final.
#output_file_path = '../Data/sell-in.csv'
#df.to_csv(output_file_path, sep=',', index=False)

$$
\text{Total Forecast Error} = \frac{\sum_{\text{sku}} |\text{Actual Sales} - \text{Forecast Sales}|}{\sum_{\text{sku}} \text{Actual Sales}}
$$



## SoluEj1


In [3]:
import pandas as pd

# Ruta al archivo
file_path = '../66_Datos/sell-in.txt'

# Cargar el archivo en un DataFrame
df = pd.read_csv(file_path, sep='\t')

# Convertir la columna 'periodo' a formato fecha
df['periodo'] = pd.to_datetime(df['periodo'], format='%Y%m')

# Filtrar los datos de marzo de 2019
df_marzo_2019 = df[df['periodo'] == '2019-03-01']

# Agrupar las ventas de marzo de 2019 por producto
prediccion_mayo_2019 = df_marzo_2019.groupby('product_id')['tn'].sum().reset_index()
prediccion_mayo_2019.rename(columns={'tn': 'predicted_tn'}, inplace=True)

# Filtrar los datos de mayo de 2019
df_mayo_2019 = df[df['periodo'] == '2019-05-01']

# Agrupar las ventas reales de mayo de 2019 por producto
ventas_reales_mayo_2019 = df_mayo_2019.groupby('product_id')['tn'].sum().reset_index()
ventas_reales_mayo_2019.rename(columns={'tn': 'actual_tn'}, inplace=True)

# Combinar las predicciones con las ventas reales
resultados = pd.merge(prediccion_mayo_2019, ventas_reales_mayo_2019, on='product_id')

# Calcular el Total Forecast Error
#    Calcular la diferencia fila por fila entre dos culumnas del df
#         resultados['actual_tn'] - resultados['predicted_tn'] 
resultados['abs_error'] = abs(resultados['actual_tn'] - resultados['predicted_tn'])
total_forecast_error = resultados['abs_error'].sum() / resultados['actual_tn'].sum()

# Mostrar el resultado
print(f'Total Forecast Error: {total_forecast_error:.2%}')


Total Forecast Error: 28.80%


In [4]:
# Calculo del total forecast error
tfe2 = calcular_total_forecast_error(resultados['actual_tn'],resultados['predicted_tn'])
print(f'Total Forecast Error: {tfe2:.2%}')


Total Forecast Error: 28.80%


In [5]:
resultados.head(10)

product_id  predicted_tn  actual_tn  abs_error
0       20001      1470.657   1629.782    159.126
1       20002      1083.626   1034.989     48.636
2       20003       638.040    590.125     47.915
3       20004       619.771    603.311     16.460
4       20005       488.214    897.263    409.049
5       20006       502.437    527.688     25.251
6       20007       576.233    394.677    181.557
7       20008       454.570    486.367     31.796
8       20009       525.472    578.486     53.014
9       20010       522.876    408.417    114.459

##  SoluEj2


Ej 2) Prediccion Entregas (tn) Mayo 2019 con datos de 6 meses previos

Con los datos de el promedio de ventas de los 6 meses previos al mes de mayo de 2019 se pide:

1) Predecir cuantas ventas vamos a tener durante el mes de mayo 2019
2) Calcular el error rate



### Estrategia
#### Paso 1: Filtrar los datos de los seis meses previos a mayo de 2019

Filtramos los datos de los seis meses anteriores a mayo de 2019 (es decir, desde noviembre de 2018 hasta abril de 2019).

#### Paso 2: Calcular la predicción para mayo de 2019 usando el promedio de ventas de los seis meses previos por producto x mes

Agrupamos los datos por producto y calculamos el promedio de `tn` para estos seis meses.

#### Paso 3: Comparar la predicción con los datos reales de mayo de 2019 y calcular el error rate

Finalmente, combinamos las predicciones con las ventas reales y calculamos el error rate utilizando la función `calcular_total_forecast_error`.



In [6]:
import pandas as pd

# Ruta al archivo
file_path = '../66_Datos/sell-in.txt'

# Cargar el archivo en un DataFrame
df = pd.read_csv(file_path, sep='\t')

# Convertir la columna 'periodo' a formato fecha
df['periodo'] = pd.to_datetime(df['periodo'], format='%Y%m')

# Filtrar los datos de los seis meses previos a mayo de 2019 (noviembre 2018 a abril 2019)
fecha_inicio = '2018-11-01'
fecha_fin = '2019-04-01'
df_seis_meses_previos = df[(df['periodo'] >= fecha_inicio) & (df['periodo'] <= fecha_fin)]

# Agrupar las ventas de los seis meses previos por producto y calcular el promedio mensual
promedio_ventas_seis_meses = df_seis_meses_previos.groupby(['product_id', df_seis_meses_previos['periodo'].dt.to_period('M')])['tn'].sum().groupby('product_id').mean().reset_index()
promedio_ventas_seis_meses.rename(columns={'tn': 'predicted_tn'}, inplace=True)

# Filtrar los datos de mayo de 2019
df_mayo_2019 = df[df['periodo'] == '2019-05-01']

# Agrupar las ventas reales de mayo de 2019 por producto
ventas_reales_mayo_2019 = df_mayo_2019.groupby('product_id')['tn'].sum().reset_index()
ventas_reales_mayo_2019.rename(columns={'tn': 'actual_tn'}, inplace=True)

# Combinar las predicciones con las ventas reales
resultados = pd.merge(promedio_ventas_seis_meses, ventas_reales_mayo_2019, on='product_id')

# Calcular el Total Forecast Error usando la función previamente definida
total_forecast_error = calcular_total_forecast_error(resultados['actual_tn'], resultados['predicted_tn'])

# Mostrar el resultado
print(f'Total Forecast Error: {total_forecast_error:.2%}')


Total Forecast Error: 25.94%


In [7]:
resultados.head(2)

product_id  predicted_tn  actual_tn
0       20001      1492.144   1629.782
1       20002      1242.886   1034.989

In [8]:
df_seis_meses_previos.periodo.value_counts()

periodo
2019-03-01    89520
2019-02-01    82519
2019-04-01    77818
2018-11-01    72280
2018-12-01    70166
2019-01-01    67628
Name: count, dtype: int64

#  Productos a Predecir

Para filtrar las ventas que se encuentran en sell-in.txt utilizando los productos listados en productos_a_predecir.txt, seguir estos pasos:

1.	Cargar ambos archivos en DataFrames.
2.	Filtrar el DataFrame de ventas (sell-in.txt) para que solo incluya los productos listados en productos_a_predecir.txt.
3.	Guardar o utilizar el DataFrame filtrado según sea necesario.


In [9]:
import pandas as pd

# Cargar los datos de ventas y productos a predecir
ventas_file_path = '../66_Datos/sell-in.txt'
productos_file_path = '../66_Datos/productos_a_predecir.txt'

df_ventas = pd.read_csv(ventas_file_path, sep='\t')
df_productos = pd.read_csv(productos_file_path, sep='\t')

# Filtrar las ventas para que solo incluya los productos a predecir
productos_a_predecir = df_productos['product_id'].unique()
df_ventas_filtradas = df_ventas[df_ventas['product_id'].isin(productos_a_predecir)]

# Mostrar las primeras filas del DataFrame filtrado
print(df_ventas_filtradas.head())

# Opcional: Guardar el DataFrame filtrado en un archivo CSV
df_ventas_filtradas.to_csv('../66_Datos/ventas_filtradas.csv', index=False)

   periodo  customer_id  product_id  plan_precios_cuidados  cust_request_qty  \
0   201701        10234       20524                      0                 2   
1   201701        10032       20524                      0                 1   
2   201701        10217       20524                      0                 1   
3   201701        10125       20524                      0                 1   
4   201701        10012       20524                      0                11   

   cust_request_tn     tn  
0            0.053  0.053  
1            0.136  0.136  
2            0.030  0.030  
3            0.023  0.023  
4            1.545  1.545  


# K1-2019-dic

Prediccion tomando unicamente valores de diciembre 


Dada la lista de productos productos_a_predecir.txt que a la Multinacional le interesa predecir y
parado al 31 de diciembre del 2019 a las 23:59:59 hay que hacer la predicción de cuanto se va a vender en febrero del 2020
Son productos que tienen mas de tres meses de historia.

Hacer dos predicciones con el mismo criterio

In [20]:
import pandas as pd

# Ruta al archivo
file_path = '../66_Datos/ventas_filtradas.csv'

# Cargar el archivo en un DataFrame
df = pd.read_csv(file_path, sep=',')

# Convertir la columna 'periodo' a formato fecha
df['periodo'] = pd.to_datetime(df['periodo'], format='%Y%m')

# Filtrar los datos de marzo de 2019
df_12_2019 = df[df['periodo'] == '2019-12-01']

# Agrupar las ventas de marzo de 2019 por producto
f_02_2020 = df_12_2019.groupby('product_id')['tn'].sum().reset_index()
#f_02_2020.rename(columns={'tn': 'predicted_tn'}, inplace=True)



In [21]:
df.head()

periodo  customer_id  product_id  plan_precios_cuidados  \
0 2017-01-01        10234       20524                      0   
1 2017-01-01        10032       20524                      0   
2 2017-01-01        10217       20524                      0   
3 2017-01-01        10125       20524                      0   
4 2017-01-01        10012       20524                      0   

   cust_request_qty  cust_request_tn     tn  
0                 2            0.053  0.053  
1                 1            0.136  0.136  
2                 1            0.030  0.030  
3                 1            0.023  0.023  
4                11            1.545  1.545

In [39]:
f_02_2020.head(2)

product_id        tn
0       20001  1504.689
1       20002  1087.309

In [24]:
f_02_2020.to_csv('../666_Kaggle/Entregas/2024-06-05.csv', index=False)


In [35]:
# =============================================================================
# IMPORTS
import time

import datetime
# fecha = datetime.datetime.today().strftime("%Y-%m-%d-%H%M")

from datetime import datetime
from pytz import timezone

buenos_aires = timezone('America/Argentina/Buenos_Aires')
fecha = datetime.now(buenos_aires).strftime("%Y-%m-%d-%H%M")


In [36]:
fecha

'2024-06-05-1415'

In [37]:
+

In [38]:
file_to_kaggle

'../666_Kaggle/Entregas/2024-06-05-1415-2019_dic'

In [45]:
df_ventas_filtradas.head()

ds  customer_id  product_id  plan_precios_cuidados  \
0 2017-01-01        10234       20524                      0   
1 2017-01-01        10032       20524                      0   
2 2017-01-01        10217       20524                      0   
3 2017-01-01        10125       20524                      0   
4 2017-01-01        10012       20524                      0   

   cust_request_qty  cust_request_tn      y  
0                 2            0.053  0.053  
1                 1            0.136  0.136  
2                 1            0.030  0.030  
3                 1            0.023  0.023  
4                11            1.545  1.545

In [1]:
import pandas as pd
from neuralprophet import NeuralProphet

# Ruta al archivo
file_path = '../66_Datos/ventas_filtradas.csv'

# Cargar el archivo en un DataFrame
df_ventas_filtradas = pd.read_csv(file_path)

# Convertir la columna 'periodo' a formato fecha y renombrar las columnas para Neural Prophet
df_ventas_filtradas['periodo'] = pd.to_datetime(df_ventas_filtradas['periodo'], format='%Y%m')
df_ventas_filtradas.rename(columns={'periodo': 'ds', 'tn': 'y'}, inplace=True)

df_ventas_filtradas.head(2)

Importing plotly failed. Interactive plots will not work.
Importing plotly failed. Interactive plots will not work.


ds  customer_id  product_id  plan_precios_cuidados  \
0 2017-01-01        10234       20524                      0   
1 2017-01-01        10032       20524                      0   

   cust_request_qty  cust_request_tn        y  
0                 2          0.05300  0.05300  
1                 1          0.13628  0.13628

#!pip install neuralprophet

import pandas as pd
from neuralprophet import NeuralProphet

# Ruta al archivo
file_path = '../66_Datos/ventas_filtradas.csv'

# Cargar el archivo en un DataFrame
df_ventas_filtradas = pd.read_csv(file_path)

# Convertir la columna 'periodo' a formato fecha y renombrar las columnas para Neural Prophet
df_ventas_filtradas['periodo'] = pd.to_datetime(df_ventas_filtradas['periodo'], format='%Y%m')
df_ventas_filtradas.rename(columns={'periodo': 'ds', 'tn': 'y'}, inplace=True)

# Crear un diccionario para almacenar las predicciones de cada producto
predicciones = {}

# Ajustar el modelo Neural Prophet para cada producto y predecir
productos_a_predecir = df_ventas_filtradas['product_id'].unique()
for product_id in productos_a_predecir:
    print(f'Entrenando y prediciendo para el producto {product_id}')
    df_producto = df_ventas_filtradas[df_ventas_filtradas['product_id'] == product_id][['ds', 'y']]
    
    # Eliminar duplicados
    df_producto = df_producto.drop_duplicates(subset=['ds'])
    
    # Crear y ajustar el modelo
    m = NeuralProphet()
    m.fit(df_producto, freq='M')
    
    # Crear dataframe de futuros
    future = m.make_future_dataframe(df_producto, periods=1, n_historic_predictions=True)
    
    # Hacer predicciones
    forecast = m.predict(future)
    
    # Guardar las predicciones en el diccionario
    predicciones[product_id] = forecast

# Convertir las predicciones a un DataFrame para su análisis
df_predicciones = pd.concat(predicciones, axis=0).reset_index(level=1, drop=True).rename_axis('product_id').reset_index()

# Guardar las predicciones en un archivo CSV
df_predicciones.to_csv('../66_Datos/predicciones_780_productos.csv', index=False)

print('Predicciones completadas y guardadas en ../66_Datos/predicciones_780_productos.csv')

In [8]:
import pandas as pd

# Ruta al archivo
file_path = '../66_Datos/ventas_filtradas.csv'

# Cargar el archivo en un DataFrame
df_ventas_filtradas = pd.read_csv(file_path)

# Convertir la columna 'periodo' a formato fecha
df_ventas_filtradas['periodo'] = pd.to_datetime(df_ventas_filtradas['periodo'], format='%Y%m')

# Obtener la cantidad de periodos únicos
num_periodos = df_ventas_filtradas['periodo'].nunique()

# Obtener la cantidad de productos únicos
num_productos = df_ventas_filtradas['product_id'].nunique()

# Obtener el rango de años disponibles en los datos
min_anio = df_ventas_filtradas['periodo'].dt.year.min()
max_anio = df_ventas_filtradas['periodo'].dt.year.max()

# Obtener el total de registros en el dataset
total_registros = df_ventas_filtradas.shape[0]

# Imprimir la información relevante
print(f"Cantidad de periodos únicos: {num_periodos}")
print(f"Cantidad de productos únicos: {num_productos}")
print(f"Rango de años disponibles: {min_anio} - {max_anio}")
print(f"Total de registros en el dataset: {total_registros}")

Cantidad de periodos únicos: 36
Cantidad de productos únicos: 780
Rango de años disponibles: 2017 - 2019
Total de registros en el dataset: 2293481


In [10]:
import pandas as pd
from neuralprophet import NeuralProphet
from tqdm.notebook import tqdm

# Ruta al archivo
file_path = '../66_Datos/ventas_filtradas.csv'

# Cargar el archivo en un DataFrame
df_ventas_filtradas = pd.read_csv(file_path)

# Convertir la columna 'periodo' a formato fecha y renombrar las columnas para Neural Prophet
df_ventas_filtradas['periodo'] = pd.to_datetime(df_ventas_filtradas['periodo'], format='%Y%m')
df_ventas_filtradas.rename(columns={'periodo': 'ds', 'tn': 'y'}, inplace=True)

# Filtrar los datos hasta el 31 de diciembre de 2019
df_ventas_filtradas = df_ventas_filtradas[df_ventas_filtradas['ds'] <= '2019-12-31']

# Obtener todos los productos únicos
productos_a_predecir = df_ventas_filtradas['product_id'].unique()

# Crear un diccionario para almacenar las predicciones de cada producto
predicciones = {}

# Ajustar el modelo Neural Prophet para cada producto y predecir
for product_id in tqdm(productos_a_predecir, desc="Procesando productos"):
    df_producto = df_ventas_filtradas[df_ventas_filtradas['product_id'] == product_id][['ds', 'y']]
    
    # Eliminar duplicados
    df_producto = df_producto.drop_duplicates(subset=['ds'])
    
    # Crear y ajustar el modelo
    m = NeuralProphet()
    m.fit(df_producto, freq='M')
    
    # Crear dataframe de futuros para predecir febrero 2020
    future = m.make_future_dataframe(df_producto, periods=2)
    forecast = m.predict(future)
    
    # Filtrar la predicción para febrero 2020
    forecast_feb2020 = forecast[forecast['ds'] == '2020-02-01']
    
    # Guardar la predicción en el diccionario
    predicciones[product_id] = forecast_feb2020[['ds', 'yhat1']]

# Convertir las predicciones a un DataFrame para su análisis
df_predicciones = pd.concat(predicciones, axis=0).reset_index(level=1, drop=True).rename_axis('product_id').reset_index()

# Seleccionar solo las columnas 'product_id' y 'yhat1'
df_resultado = df_predicciones[['product_id', 'yhat1']]

# Renombrar la columna 'yhat1' a 'tn' para reflejar las predicciones de toneladas
df_resultado.rename(columns={'yhat1': 'tn'}, inplace=True)

# Guardar el resultado en un nuevo archivo CSV
output_file_path = '../66_Datos/predicciones_ajustadas_780_productos_feb2020.csv'
df_resultado.to_csv(output_file_path, index=False)

print(f'Predicciones ajustadas guardadas en {output_file_path}')

Procesando productos:   0%|          | 0/780 [00:00<?, ?it/s]

WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-packages/neuralprophet/df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df_utils._infer_frequency) - Major frequency MS corresponds to [97.222]% of the data.
WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-packages/neuralprophet/df_utils.py:1173: FutureWarning: 'M' is deprecated and will be removed in a future version, please use 'ME' instead.
  aux_ts = pd.DataFrame(pd.date_range("1994-01-01", periods=100, freq=freq_str))

WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-pack

Finding best initial lr:   0%|          | 0/203 [00:00<?, ?it/s]

Training: 0it [00:00, ?it/s]

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-packages/neuralprophet/df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df_utils._infer_frequency) - Major frequency MS corresponds to [97.222]% of the data.
WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-packages/neuralprophet/df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``ast

...

Training: 0it [00:00, ?it/s]

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

WARNING - (py.warnings._showwarnmsg) - /Users/aure/anaconda3/envs/ydata-profiling/lib/python3.12/site-packages/neuralprophet/df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df

Predicting: 1it [00:00, ?it/s]

INFO - (NP.df_utils.return_df_in_original_format) - Returning df with no ID column
WARNING - (py.warnings._showwarnmsg) - /var/folders/w1/fwmwl18j7yvfc0766bv7m8_r0000gn/T/ipykernel_96267/2771073749.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_resultado.rename(columns={'yhat1': 'tn'}, inplace=True)



Predicciones ajustadas guardadas en ../66_Datos/predicciones_ajustadas_780_productos_feb2020.csv
